In [1]:
# Reset all variables and clear memory
%reset -f  

# Import necessary modules
from IPython.display import display, HTML
import pandas as pd
import sys
import os
import matplotlib.pyplot as plt

# Expand Jupyter Notebook width to 100% of the screen
display(HTML("<style>:root { --jp-notebook-max-width: 100% !important; }</style>"))

# Enable inline plotting for Matplotlib and improve figure quality
%matplotlib inline
%config InlineBackend.figure_format = 'svg'

# Ensure that Jupyter output cells do not have height restrictions
display(HTML("<style>.output_scroll { height: auto !important; }</style>"))

# Enable automatic module reloading in Jupyter Notebook
%reload_ext autoreload
%autoreload 2

In [2]:
# Define the file path
file_path = "../data/indicators.csv"

# Read CSV, set the first column as the index, and parse it as datetime
df = pd.read_csv(file_path, index_col=0, parse_dates=[0], sep=',')

# Ensure the index is in UTC
df.index = pd.to_datetime(df.index, utc=True)

# Display first rows and index dtype
print(df.head())
print("\nIndex dtype:", df.index.dtype)  # Should output 'datetime64[ns, UTC]'

                                open       high        low      close  \
time_UTC                                                                
2025-01-22 23:00:00+00:00  104013.42  104514.80  103813.33  103866.79   
2025-01-22 23:30:00+00:00  103866.79  104143.99  103679.46  103845.00   
2025-01-23 00:00:00+00:00  103845.01  103982.46  103654.00  103706.66   
2025-01-23 00:30:00+00:00  103706.66  103819.99  103102.00  103376.13   
2025-01-23 01:00:00+00:00  103376.14  103634.09  103052.82  103307.51   

                              volume  number_of_trades  taker_buy_vol  \
time_UTC                                                                
2025-01-22 23:00:00+00:00  321.07772           71993.0      146.34892   
2025-01-22 23:30:00+00:00  285.46943          112621.0      144.55558   
2025-01-23 00:00:00+00:00  152.57958           53974.0       74.85703   
2025-01-23 00:30:00+00:00  573.65755           85687.0      240.73677   
2025-01-23 01:00:00+00:00  386.01912           783

In [3]:
def convert_to_msec(time_str):
    """
    Converts time intervals such as "5m", "1h", "3d", "1w" into milliseconds (integer).
    """
    unit = time_str[-1]  # Extract the last character (time unit)
    value = int(time_str[:-1])  # Extract the numerical part

    if unit == 's':  # Seconds
        return value * 1000
    elif unit == 'm':  # Minutes
        return value * 60 * 1000
    elif unit == 'h':  # Hours
        return value * 3600 * 1000
    elif unit == 'd':  # Days
        return value * 86400 * 1000
    elif unit == 'w':  # Weeks
        return value * 604800 * 1000
    else:
        raise ValueError("Unsupported time format")  # Raise an error for unsupported formats


# Define necessary constants
interval_str = "30m"  # Time interval for analysis
is_OI_included = True  # Flag indicating whether Open Interest data is included

NORMALIZATION_PERIOD_H = 720  # Normalization period in hours (30 days)
DELTA_ROL_SUM_PERIODS_H = [12, 36]  # Rolling sum calculation periods for delta (in hours) for 30m interval
DEL_PRICE_ROL_SUM_PERIODS_H = DELTA_ROL_SUM_PERIODS_H + [24, 48]  # Extended rolling sum periods for price analysis
WINDOW_FOR_DELTA_PRICE_DISTR_H = 8640  # Window for delta price distribution (360 days in hours)

# Compute time step in seconds based on the interval string
TIME_STEP_SEC = int(convert_to_msec(interval_str) / 1000)


In [4]:
# DataFrame validation and summary

# Check for NaN values
print("\nChecking for missing (NaN) values in the DataFrame:")
if df.isnull().values.any():
    print(df.isna().sum())  # Show the count of NaNs per column
else:
    print("No NaN values found in the DataFrame.")

# Check if the time intervals between indices are consistent
time_deltas = pd.to_timedelta(df.index.to_series().diff().dropna())

# Ensure all time steps are identical
if time_deltas.nunique() == 1:
    print(f"\nThe time step between indices is consistent: {time_deltas.iloc[0]}")
    print(f"Time step in seconds: {TIME_STEP_SEC}")
else:
    print("\nThere are missing time indices or irregular time steps.")

# Show data types of each column
print("\nData Types by Attribute:\n")
print(df.dtypes)
print(f"Index Data Type: {df.index.dtype}")

# Display DataFrame size
print(f"\nNumber of rows in the DataFrame: {len(df)}")

# Show the date range in the dataset
print(f"\nFirst date in index: {df.index[0]}")
print(f"Last date in index: {df.index[-1]}")


Checking for missing (NaN) values in the DataFrame:
No NaN values found in the DataFrame.

The time step between indices is consistent: 0 days 00:30:00
Time step in seconds: 1800

Data Types by Attribute:

open                        float64
high                        float64
low                         float64
close                       float64
volume                      float64
                             ...   
resistance_pos_sum_36h      float64
resistance_neg_sum_36h      float64
sentiment_d_sum_36h         float64
resistance_pos_d_sum_36h    float64
resistance_neg_d_sum_36h    float64
Length: 92, dtype: object
Index Data Type: datetime64[ns, UTC]

Number of rows in the DataFrame: 2161

First date in index: 2025-01-22 23:00:00+00:00
Last date in index: 2025-03-08 23:00:00+00:00


In [5]:
# Get the most recent date in the index
latest_date = df.index.max()

# Filter the DataFrame for the last 15 days
df = df[df.index >= latest_date - pd.Timedelta(days=15)]

In [6]:
# Add 'src' directory to system path for module import
sys.path.append(os.path.abspath("../src"))
from graphs_func import *  # Import necessary functions from graphs_func module

# Configuration variables
n = 35  # Number of subplots

draw_rel_delta = False  # Flag to include relative delta plot

draw_bars = False  # Flag to include bar charts

trade_info = None  # Trade information (if available)

df_bound = df  # Data boundary reference

# Determine the minimum and maximum delta rolling sum periods
min_h = min(DELTA_ROL_SUM_PERIODS_H)
max_h = max(DELTA_ROL_SUM_PERIODS_H)

# Initialize an index counter for subplots
idx = IndexCounter()

# Adjust the number of subplots based on available data
if ('sumOpenInterest' in df.columns) and not df['sumOpenInterest'].isna().any():
    n += 2
    if draw_bars:
        n += 12
    if draw_rel_delta:
        n += 8
else:
    if draw_bars:
        n += 12
    if draw_rel_delta:
        n += 8

# Create subplots
fig, axs = plt.subplots(n, 1, figsize=(18, n * 1.75), sharex=True)

# Draw various metrics
draw_price(axs[idx.i_curr()], df, TIME_STEP_SEC, trade_info)
draw_line(axs[idx.i_next()], df, f'delta_norm_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
draw_line(axs[idx.i_next()], df, f'sentiment_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
draw_line(axs[idx.i_next()], df, f'vol_ln_stand_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='mediumaquamarine')

if draw_rel_delta:
    draw_line(axs[idx.i_next()], df, f'delta_rel_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

draw_line(axs[idx.i_next()], df, f'delta_pos_norm_sum_{max_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='green', color_neg='mediumaquamarine')
draw_line(axs[idx.i_next()], df, f'resistance_pos_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='lightseagreen', color_neg='coral')
draw_line(axs[idx.i_next()], df, f'delta_neg_norm_sum_{max_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='red', color_neg='lightcoral')
draw_line(axs[idx.i_next()], df, f'resistance_neg_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='lightseagreen', color_neg='coral')
draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

if ('sumOpenInterest' in df.columns) and not df['sumOpenInterest'].isna().any():
    draw_line(axs[idx.i_next()], df, 'sumOpenInterest', trade_info, line_color='darkorange', linewidth_=1)

draw_line(axs[idx.i_next()], df, f'delta_d_norm_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
draw_line(axs[idx.i_next()], df, f'sentiment_d_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
draw_line(axs[idx.i_next()], df, f'vol_d_ln_stand_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='lightseagreen')

if draw_rel_delta:
    draw_line(axs[idx.i_next()], df, f'delta_d_rel_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

draw_line(axs[idx.i_next()], df, f'delta_d_pos_norm_sum_{max_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='darkgreen', color_neg='lightseagreen')
draw_line(axs[idx.i_next()], df, f'resistance_pos_d_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='teal', color_neg='chocolate')
draw_line(axs[idx.i_next()], df, f'delta_d_neg_norm_sum_{max_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='darkred', color_neg='indianred')
draw_line(axs[idx.i_next()], df, f'resistance_neg_d_sum_{max_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='teal', color_neg='chocolate')

if draw_bars:
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'vol_ln_stand', trade_info, df_bound=df_bound, bar_color_pos='green', bar_color_neg='mediumaquamarine')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'delta_norm', trade_info, df_bound=df_bound, bar_color_pos='green', bar_color_neg='red')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'sentiment', trade_info, df_bound=df_bound, bar_color_pos='green', bar_color_neg='red')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'resistance_pos', trade_info, df_bound=df_bound, bar_color_pos='lightseagreen', bar_color_neg='coral')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'resistance_neg', trade_info, df_bound=df_bound, bar_color_pos='lightseagreen', bar_color_neg='coral')

draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)
draw_line(axs[idx.i_next()], df, f'delta_norm_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
draw_line(axs[idx.i_next()], df, f'sentiment_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
draw_line(axs[idx.i_next()], df, f'vol_ln_stand_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='mediumaquamarine')

if draw_rel_delta:
    draw_line(axs[idx.i_next()], df, f'delta_rel_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='green', color_neg='red')
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

draw_line(axs[idx.i_next()], df, f'delta_pos_norm_sum_{min_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='green', color_neg='mediumaquamarine')
draw_line(axs[idx.i_next()], df, f'resistance_pos_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='lightseagreen', color_neg='coral')
draw_line(axs[idx.i_next()], df, f'delta_neg_norm_sum_{min_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='red', color_neg='lightcoral')
draw_line(axs[idx.i_next()], df, f'resistance_neg_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='lightseagreen', color_neg='coral')

if draw_bars:
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'vol_d_ln_stand', trade_info, df_bound=df_bound, bar_color_pos='darkgreen', bar_color_neg='lightseagreen')    
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'delta_d_norm', trade_info, df_bound=df_bound, bar_color_pos='darkgreen', bar_color_neg='darkred')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'sentiment_d', trade_info, df_bound=df_bound, bar_color_pos='darkgreen', bar_color_neg='darkred')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'resistance_pos_d', trade_info, df_bound=df_bound, bar_color_pos='teal', bar_color_neg='chocolate')
    draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'resistance_neg_d', trade_info, df_bound=df_bound, bar_color_pos='teal', bar_color_neg='chocolate')

draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

if ('sumOpenInterest' in df.columns) and not df['sumOpenInterest'].isna().any():
    draw_line(axs[idx.i_next()], df, 'sumOpenInterest', trade_info, line_color='darkorange', linewidth_=1)

draw_line(axs[idx.i_next()], df, f'delta_d_norm_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
draw_line(axs[idx.i_next()], df, f'sentiment_d_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
draw_line(axs[idx.i_next()], df, f'vol_d_ln_stand_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='lightseagreen')

if draw_rel_delta:
    draw_line(axs[idx.i_next()], df, f'delta_d_rel_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='darkgreen', color_neg='darkred')
    draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)

draw_line(axs[idx.i_next()], df, f'delta_d_pos_norm_sum_{min_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='darkgreen', color_neg='lightseagreen')
draw_line(axs[idx.i_next()], df, f'resistance_pos_d_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='teal', color_neg='chocolate')
draw_line(axs[idx.i_next()], df, f'delta_d_neg_norm_sum_{min_h}h_discr', trade_info, y_min=0, y_max=6, sep_line=3, color_pos='darkred', color_neg='indianred')
draw_line(axs[idx.i_next()], df, f'resistance_neg_d_sum_{min_h}h', trade_info, df_bound=df_bound, sep_line=0, color_pos='teal', color_neg='chocolate')
draw_price(axs[idx.i_next()], df, TIME_STEP_SEC, trade_info)
draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'premium_index', trade_info, df_bound=df_bound, bar_color_pos='green', bar_color_neg='red')
draw_bar(axs[idx.i_next()], df, TIME_STEP_SEC, 'premium_index_stand', trade_info, df_bound=df_bound, bar_color_pos='green', bar_color_neg='red')

plt.tight_layout()
plt.show()